In [1]:
import pandas as pd
import plotly.express as px
from statsmodels.tsa.seasonal import seasonal_decompose
import logging
import datetime
import time

import dash
from dash import dcc, html
from dash.dependencies import Input, Output

import calendar
import pandas as pd
import plotly.express as px
from pyspark.sql import SparkSession
from pyspark.sql.functions import concat, col
import matplotlib.pyplot as plt
import seaborn as sns
from statsmodels.tsa.seasonal import seasonal_decompose
from ipywidgets import interact, widgets
from matplotlib.dates import MonthLocator, DateFormatter
import geopandas as gpd
from shapely.geometry import Point
from sklearn.preprocessing import StandardScaler
from statsmodels.tsa.holtwinters import ExponentialSmoothing
import geopandas as gpd
from mpl_toolkits.axes_grid1 import make_axes_locatable
#from fbprophet import Prophet
from sklearn.metrics import mean_squared_error
import numpy as np
import plotly.graph_objects as go
from pyspark.sql import functions as F
from pyspark.sql.functions import year, month
from sklearn.metrics.pairwise import euclidean_distances
from pyspark.sql.functions import year, month, sum as sum_
from scipy.spatial.distance import euclidean
from prophet import Prophet
from pyspark.sql.functions import col, countDistinct , desc , count , length
from pyspark.sql.functions import split, col, when
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, udf, dayofmonth, last_day ,to_date, lit, isnull
from pyspark.sql.types import IntegerType
import numpy as np
from sklearn.metrics import r2_score, mean_squared_error
from dateutil.relativedelta import relativedelta
from pyspark.sql.functions import date_format

import schedule
from pyspark.sql.functions import col, to_timestamp, date_format

import pyspark
import pandas as pd
import boto3
import sagemaker
import sagemaker.feature_store.feature_store as fs
import databricks.connect
from dateutil.relativedelta import relativedelta

import pandas as pd
import numpy as np
import plotly.graph_objects as go
from sklearn.metrics import mean_squared_error, mean_absolute_percentage_error, mean_absolute_error
from sklearn.metrics import mean_squared_error, root_mean_squared_error

import pandas as pd
import numpy as np
from prophet import Prophet
from sklearn.metrics import mean_absolute_percentage_error, mean_squared_error
import plotly.graph_objects as go
from itertools import product
import random
import statsmodels.api as sm
import os

import logging

logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
from databricks.connect import DatabricksSession

# Get spark
spark = databricks.connect.DatabricksSession.builder.getOrCreate()

c:\Users\gusta\AppData\Local\pypoetry\Cache\virtualenvs\ltv-novo-aF9Dy8BA-py3.10\lib\site-packages\pydantic\_internal\_fields.py:192: UserWarning: Field name "json" in "MonitoringDatasetFormat" shadows an attribute in parent "Base"
  warnings.warn(


[02/11/25 14:23:23] INFO     Found credentials in shared credentials file: ~/.aws/credentials   ]8;id=163400;file://c:\Users\gusta\AppData\Local\pypoetry\Cache\virtualenvs\ltv-novo-aF9Dy8BA-py3.10\lib\site-packages\botocore\credentials.py\credentials.py]8;;\:]8;id=734588;file://c:\Users\gusta\AppData\Local\pypoetry\Cache\virtualenvs\ltv-novo-aF9Dy8BA-py3.10\lib\site-packages\botocore\credentials.py#1278\1278]8;;\

sagemaker.config INFO - Not applying SDK defaults from location: C:\ProgramData\sagemaker\sagemaker\config.yaml
sagemaker.config INFO - Not applying SDK defaults from location: C:\Users\gusta\AppData\Local\sagemaker\sagemaker\config.yaml


In [2]:
contrato_sdf = spark.table("dev.dw_redeok_model.tb_d_contract")
customer_sdf= spark.table("dev.dw_redeok_model.tb_d_customer")
recebivel_sdf = spark.table("dev.dw_redeok_model.tb_f_accounts_receivable")
churn_sdf = spark.table("dev.dw_redeok_model.tb_f_churn")

In [3]:


# Ordenando pela coluna churn_date da mais antiga para a mais nova
#churn_sdf = churn_sdf.orderBy(col("churn_date").asc())

# Exibindo os dados ordenados
churn_sdf.show(100000,truncate=False)
churn_sdf.count()

+------------------------------------+------------------------------------+------------------------------------+-------------------+--------------------+------------------------------+------------------+--------------------------+------------------+--------------------------+
|uuid                                |uuid_contract                       |uuid_customer                       |churn_date         |motivation          |churn_type                    |data_source_insert|created_at                |data_source_update|updated_at                |
+------------------------------------+------------------------------------+------------------------------------+-------------------+--------------------+------------------------------+------------------+--------------------------+------------------+--------------------------+
|2c66166c-adc3-4e1b-895e-0ba383386114|62e395ab-f114-45b6-b345-a0a525be3774|f3ce93b1-8097-4915-ad4b-f4876a8d82e8|2021-01-03 11:30:20|OUTROS MOTIVOS      |90 DIAS BLOQUEAD

24296

## Teste 1

In [5]:
# Definir o UUID que deseja filtrar
uuid_alvo = "281fbe4e-4549-4cbc-a28e-19e024b5a5de"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+----------+--------------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|motivation|          churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+----------+--------------------+------------------+--------------------+------------------+--------------------+
|5e8bc308-575b-4ee...|74b8c36a-9387-42c...|281fbe4e-4549-4cb...|2021-01-05 14:12:24|      NULL|90 DIAS PRÉ CANCE...|            signet|2024-04-26 20:36:...|                  |2024-04-26 20:36:...|
+--------------------+--------------------+--------------------+-------------------+----------+--------------------+------------------+--------------------+------------------+--------------------+



In [9]:
# Definir o UUID que deseja filtrar
uuid_alvo = "281fbe4e-4549-4cbc-a28e-19e024b5a5de"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+--------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+--------+-------------+-----------------+----------+-------------+-------+-----------------+-----------------

In [8]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "74b8c36a-9387-42cd-aa24-8b1f9595ff01"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|74b8c36a-9387-42c...|2018-01-01|BAIXADO|
|74b8c36a-9387-42c...|2018-02-01|BAIXADO|
|74b8c36a-9387-42c...|2018-03-01|BAIXADO|
|74b8c36a-9387-42c...|2018-04-01|BAIXADO|
|74b8c36a-9387-42c...|2018-05-01|BAIXADO|
|74b8c36a-9387-42c...|2018-06-01|BAIXADO|
|74b8c36a-9387-42c...|2018-07-01|BAIXADO|
|74b8c36a-9387-42c...|2018-08-01|BAIXADO|
|74b8c36a-9387-42c...|2018-09-01|BAIXADO|
|74b8c36a-9387-42c...|2018-10-01|BAIXADO|
|74b8c36a-9387-42c...|2018-11-01|BAIXADO|
|74b8c36a-9387-42c...|2018-12-01|BAIXADO|
|74b8c36a-9387-42c...|2019-01-01|BAIXADO|
|74b8c36a-9387-42c...|2019-02-01|BAIXADO|
|74b8c36a-9387-42c...|2019-03-01|BAIXADO|
|74b8c36a-9387-42c...|2019-04-01|BAIXADO|
|74b8c36a-9387-42c...|2019-05-01|BAIXADO|
|74b8c36a-9387-42c...|2019-06-01|BAIXADO|
|74b8c36a-9387-42c...|2019-07-01|BAIXADO|
|74b8c36a-9387-42c...|2019-08-01|BAIXADO|
|74b8c36a-9387-42c...|2019-09-01|B

## Teste 

In [10]:
# Definir o UUID que deseja filtrar
uuid_alvo = "95084789-5eb9-47fd-aa5b-cdc24415e29d"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+-------------------+-----------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|         motivation|       churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+-------------------+-----------------+------------------+--------------------+------------------+--------------------+
|ac361360-b3b7-4fe...|edecbc55-7a47-495...|95084789-5eb9-47f...|2025-01-20 02:00:07|BLOQ. AUTO. 15 DIAS|90 DIAS BLOQUEADO|            signet|2025-01-22 12:41:...|                  |2025-01-22 12:41:...|
+--------------------+--------------------+--------------------+-------------------+-------------------+-----------------+------------------+--------------------+------------------+-------

In [13]:
# Definir o UUID que deseja filtrar
uuid_alvo = "95084789-5eb9-47fd-aa5b-cdc24415e29d"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [12]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "edecbc55-7a47-495f-accb-41802915548c"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|edecbc55-7a47-495...|2023-09-01|BAIXADO|
|edecbc55-7a47-495...|2023-10-01|BAIXADO|
|edecbc55-7a47-495...|2023-11-01|BAIXADO|
|edecbc55-7a47-495...|2023-12-01|BAIXADO|
|edecbc55-7a47-495...|2024-01-01|BAIXADO|
|edecbc55-7a47-495...|2024-02-01|BAIXADO|
|edecbc55-7a47-495...|2024-03-01|BAIXADO|
|edecbc55-7a47-495...|2024-04-01|BAIXADO|
|edecbc55-7a47-495...|2024-05-01|BAIXADO|
|edecbc55-7a47-495...|2024-06-01|BAIXADO|
|edecbc55-7a47-495...|2024-07-01|BAIXADO|
|edecbc55-7a47-495...|2024-08-01|BAIXADO|
|edecbc55-7a47-495...|2024-09-01|BAIXADO|
|edecbc55-7a47-495...|2024-10-01|BAIXADO|
|edecbc55-7a47-495...|2024-11-01| ABERTO|
|edecbc55-7a47-495...|2024-12-01| ABERTO|
|edecbc55-7a47-495...|2025-01-01| ABERTO|
+--------------------+----------+-------+



## Teste 

In [14]:
# Definir o UUID que deseja filtrar
uuid_alvo = "29ac5d9d-331d-4a5c-8b27-c806489088b5"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+----------------+--------------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|      motivation|          churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+----------------+--------------------+------------------+--------------------+------------------+--------------------+
|9ea4ce55-a089-421...|be8de249-96b8-4ab...|29ac5d9d-331d-4a5...|2025-01-19 11:08:02|ALT POLIT VENDAS|90 DIAS PRÉ CANCE...|            signet|2025-01-22 12:41:...|                  |2025-01-22 12:41:...|
+--------------------+--------------------+--------------------+-------------------+----------------+--------------------+------------------+--------------------+------------------+-------

In [18]:
# Definir o UUID que deseja filtrar
uuid_alvo = "29ac5d9d-331d-4a5c-8b27-c806489088b5"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [17]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "be8de249-96b8-4abe-b5cc-bdc8c28847d9"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|be8de249-96b8-4ab...|2018-01-01|BAIXADO|
|be8de249-96b8-4ab...|2018-02-01|BAIXADO|
|be8de249-96b8-4ab...|2018-03-01|BAIXADO|
|be8de249-96b8-4ab...|2018-04-01|BAIXADO|
|be8de249-96b8-4ab...|2018-05-01|BAIXADO|
|be8de249-96b8-4ab...|2018-06-01|BAIXADO|
|be8de249-96b8-4ab...|2018-07-01|BAIXADO|
|be8de249-96b8-4ab...|2018-08-01|BAIXADO|
|be8de249-96b8-4ab...|2018-09-01|BAIXADO|
|be8de249-96b8-4ab...|2018-10-01|BAIXADO|
|be8de249-96b8-4ab...|2018-11-01|BAIXADO|
|be8de249-96b8-4ab...|2018-12-01|BAIXADO|
|be8de249-96b8-4ab...|2019-01-01|BAIXADO|
|be8de249-96b8-4ab...|2019-02-01|BAIXADO|
|be8de249-96b8-4ab...|2019-03-01|BAIXADO|
|be8de249-96b8-4ab...|2019-04-01|BAIXADO|
|be8de249-96b8-4ab...|2019-05-01|BAIXADO|
|be8de249-96b8-4ab...|2019-06-01|BAIXADO|
|be8de249-96b8-4ab...|2019-07-01|BAIXADO|
|be8de249-96b8-4ab...|2019-08-01|BAIXADO|
|be8de249-96b8-4ab...|2019-09-01|B

## Teste 

In [4]:
# Definir o UUID que deseja filtrar
uuid_alvo = "f3ce93b1-8097-4915-ad4b-f4876a8d82e8"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+--------------+-----------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|    motivation|       churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+--------------+-----------------+------------------+--------------------+------------------+--------------------+
|2c66166c-adc3-4e1...|62e395ab-f114-45b...|f3ce93b1-8097-491...|2021-01-03 11:30:20|OUTROS MOTIVOS|90 DIAS BLOQUEADO|            signet|2024-04-26 20:36:...|                  |2024-04-26 20:36:...|
+--------------------+--------------------+--------------------+-------------------+--------------+-----------------+------------------+--------------------+------------------+--------------------+



In [8]:
# Definir o UUID que deseja filtrar
uuid_alvo = "f3ce93b1-8097-4915-ad4b-f4876a8d82e8"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [7]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "62e395ab-f114-45b6-b345-a0a525be3774"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|62e395ab-f114-45b...|2018-01-01|BAIXADO|
|62e395ab-f114-45b...|2018-02-01|BAIXADO|
|62e395ab-f114-45b...|2018-03-01|BAIXADO|
|62e395ab-f114-45b...|2018-04-01|BAIXADO|
|62e395ab-f114-45b...|2018-05-01|BAIXADO|
|62e395ab-f114-45b...|2018-06-01|BAIXADO|
|62e395ab-f114-45b...|2018-07-01|BAIXADO|
|62e395ab-f114-45b...|2018-08-01|BAIXADO|
|62e395ab-f114-45b...|2018-09-01|BAIXADO|
|62e395ab-f114-45b...|2018-10-01|BAIXADO|
|62e395ab-f114-45b...|2018-11-01|BAIXADO|
|62e395ab-f114-45b...|2018-12-01|BAIXADO|
|62e395ab-f114-45b...|2019-01-01|BAIXADO|
|62e395ab-f114-45b...|2019-02-01|BAIXADO|
|62e395ab-f114-45b...|2019-03-01|BAIXADO|
|62e395ab-f114-45b...|2019-04-01|BAIXADO|
|62e395ab-f114-45b...|2019-05-01|BAIXADO|
|62e395ab-f114-45b...|2019-06-01|BAIXADO|
|62e395ab-f114-45b...|2019-07-01|BAIXADO|
|62e395ab-f114-45b...|2019-08-01|BAIXADO|
|62e395ab-f114-45b...|2019-09-01|B

### Teste

In [9]:
# Definir o UUID que deseja filtrar
uuid_alvo = "7a2b58cc-bc20-4e4e-9740-fbe112cd8c77"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+--------------+-------------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|    motivation|         churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+--------------+-------------------+------------------+--------------------+------------------+--------------------+
|fcba0c5f-06a6-4cd...|8f2026c1-602b-45a...|7a2b58cc-bc20-4e4...|2022-02-11 09:08:31|NAO UTIL. SERV|CANCELAMENTO NORMAL|            signet|2024-04-26 20:36:...|                  |2024-04-26 20:36:...|
+--------------------+--------------------+--------------------+-------------------+--------------+-------------------+------------------+--------------------+------------------+--------------------+


In [12]:
# Definir o UUID que deseja filtrar
uuid_alvo = "7a2b58cc-bc20-4e4e-9740-fbe112cd8c77"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [11]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "8f2026c1-602b-45ab-b86e-2b557edcd9ca"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|8f2026c1-602b-45a...|2018-01-01|BAIXADO|
|8f2026c1-602b-45a...|2018-02-01|BAIXADO|
|8f2026c1-602b-45a...|2018-03-01|BAIXADO|
|8f2026c1-602b-45a...|2018-04-01|BAIXADO|
|8f2026c1-602b-45a...|2018-05-01|BAIXADO|
|8f2026c1-602b-45a...|2018-06-01|BAIXADO|
|8f2026c1-602b-45a...|2018-07-01|BAIXADO|
|8f2026c1-602b-45a...|2018-08-01|BAIXADO|
|8f2026c1-602b-45a...|2018-09-01|BAIXADO|
|8f2026c1-602b-45a...|2018-10-01|BAIXADO|
|8f2026c1-602b-45a...|2018-11-01|BAIXADO|
|8f2026c1-602b-45a...|2018-12-01|BAIXADO|
|8f2026c1-602b-45a...|2019-01-01|BAIXADO|
|8f2026c1-602b-45a...|2019-02-01|BAIXADO|
|8f2026c1-602b-45a...|2019-03-01|BAIXADO|
|8f2026c1-602b-45a...|2019-04-01|BAIXADO|
|8f2026c1-602b-45a...|2019-05-01|BAIXADO|
|8f2026c1-602b-45a...|2019-06-01|BAIXADO|
|8f2026c1-602b-45a...|2019-07-01|BAIXADO|
|8f2026c1-602b-45a...|2019-08-01|BAIXADO|
|8f2026c1-602b-45a...|2019-09-01|B

## Teste

In [15]:
# Definir o UUID que deseja filtrar
uuid_alvo = "7559e7ec-389b-41a7-83ee-cfcfde04e43e"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+----------+-------------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|motivation|         churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+----------+-------------------+------------------+--------------------+------------------+--------------------+
|4996fd89-07ca-4ed...|d5771ab0-5715-416...|7559e7ec-389b-41a...|2024-09-16 10:52:46|  ENC ATIV|CANCELAMENTO NORMAL|            signet|2024-09-16 14:26:...|                  |2024-09-16 14:26:...|
+--------------------+--------------------+--------------------+-------------------+----------+-------------------+------------------+--------------------+------------------+--------------------+



In [16]:
# Definir o UUID que deseja filtrar
uuid_alvo = "7559e7ec-389b-41a7-83ee-cfcfde04e43e"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show(truncate=False)

+------------------------------------+------------------------------------+------------------------------------+------------------------------------+------------------------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+-----------------------+------------------+--------------------------+---------+-----------+------------------------------------+
|uuid                                |uuid_customer                       |uuid_partner                        |uuid_wallet                         |uuid_business_model                 |status  |start_date         |end_date           |status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|created_at             |data_source_update|updated_at                |uuid_user|entity_type|uuid_partner_contract               |
+-------------

In [21]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "d5771ab0-5715-4161-9944-98d699d3694e"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)


+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|d5771ab0-5715-416...|2018-01-01|BAIXADO|
|d5771ab0-5715-416...|2018-02-01|BAIXADO|
|d5771ab0-5715-416...|2018-03-01|BAIXADO|
|d5771ab0-5715-416...|2018-04-01|BAIXADO|
|d5771ab0-5715-416...|2018-05-01|BAIXADO|
|d5771ab0-5715-416...|2018-06-01|BAIXADO|
|d5771ab0-5715-416...|2018-07-01|BAIXADO|
|d5771ab0-5715-416...|2018-08-01|BAIXADO|
|d5771ab0-5715-416...|2018-09-01|BAIXADO|
|d5771ab0-5715-416...|2018-10-01|BAIXADO|
|d5771ab0-5715-416...|2018-11-01|BAIXADO|
|d5771ab0-5715-416...|2018-12-01|BAIXADO|
|d5771ab0-5715-416...|2019-01-01|BAIXADO|
|d5771ab0-5715-416...|2019-02-01|BAIXADO|
|d5771ab0-5715-416...|2019-03-01|BAIXADO|
|d5771ab0-5715-416...|2019-04-01|BAIXADO|
|d5771ab0-5715-416...|2019-05-01|BAIXADO|
|d5771ab0-5715-416...|2019-06-01|BAIXADO|
|d5771ab0-5715-416...|2019-07-01|BAIXADO|
|d5771ab0-5715-416...|2019-08-01|BAIXADO|
|d5771ab0-5715-416...|2019-09-01|B

## Teste 2

In [23]:
# Definir o UUID que deseja filtrar
uuid_alvo = "da8edfba-c270-4679-ad9f-c1e1a99e0c7d"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+----------------+-----------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|      motivation|       churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+----------------+-----------------+------------------+--------------------+------------------+--------------------+
|794cb7c5-7507-48d...|9f4def0d-0b71-47a...|da8edfba-c270-467...|2024-10-01 11:32:02|FATURA EM ABERTO|90 DIAS BLOQUEADO|            signet|2024-10-02 10:08:...|                  |2024-10-02 10:08:...|
+--------------------+--------------------+--------------------+-------------------+----------------+-----------------+------------------+--------------------+------------------+--------------------+


In [26]:
# Definir o UUID que deseja filtrar
uuid_alvo = "da8edfba-c270-4679-ad9f-c1e1a99e0c7d"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show(truncate=False)

+------------------------------------+------------------------------------+------------------------------------+------------------------------------+------------------------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+-----------------------+------------------+-------------------------+---------+-----------+------------------------------------+
|uuid                                |uuid_customer                       |uuid_partner                        |uuid_wallet                         |uuid_business_model                 |status  |start_date         |end_date           |status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|created_at             |data_source_update|updated_at               |uuid_user|entity_type|uuid_partner_contract               |
+---------------

In [27]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "9f4def0d-0b71-47a9-b4c0-a4074e646e25"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)


+--------------------+----------+---------+
|       uuid_contract|issue_date|   status|
+--------------------+----------+---------+
|9f4def0d-0b71-47a...|2021-09-01|  BAIXADO|
|9f4def0d-0b71-47a...|2021-12-01|   ABERTO|
|9f4def0d-0b71-47a...|2022-01-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-02-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-04-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-05-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-06-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-07-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-08-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-09-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-10-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-11-01|  BAIXADO|
|9f4def0d-0b71-47a...|2022-12-01|  BAIXADO|
|9f4def0d-0b71-47a...|2023-01-01|  BAIXADO|
|9f4def0d-0b71-47a...|2023-02-01|  BAIXADO|
|9f4def0d-0b71-47a...|2023-03-01|  BAIXADO|
|9f4def0d-0b71-47a...|2023-04-01|   ABERTO|
|9f4def0d-0b71-47a...|2023-05-01|   ABERTO|
|9f4def0d-0b71-47a...|2023-06-01|  BAIXADO|
|9f4def0d-0b71-47a...|2023-07-01

### Teste 3 

In [34]:
# Definir o UUID que deseja filtrar
uuid_alvo = "f35ab9c4-15e8-4f27-8ea4-c4cb4b609ffc"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show(truncate=False)

+------------------------------------+------------------------------------+------------------------------------+-------------------+-------------------+---------------------+------------------+--------------------------+------------------+--------------------------+
|uuid                                |uuid_contract                       |uuid_customer                       |churn_date         |motivation         |churn_type           |data_source_insert|created_at                |data_source_update|updated_at                |
+------------------------------------+------------------------------------+------------------------------------+-------------------+-------------------+---------------------+------------------+--------------------------+------------------+--------------------------+
|9987dc07-1ad4-4fa6-980b-dda1a486ebf1|2ff27739-a43f-4ad7-973a-4a3c9b9bdf3e|f35ab9c4-15e8-4f27-8ea4-c4cb4b609ffc|2025-01-22 08:11:04|BLOQUEIO_REGRA_90  |CANCELAMENTO NORMAL  |signet            |2025-0

In [33]:
# Definir o UUID que deseja filtrar
uuid_alvo = "f35ab9c4-15e8-4f27-8ea4-c4cb4b609ffc"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+------+-------------------+--------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|status|         start_date|end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+------+-------------------+--------+-------------+-----------------+----------+-------------+-------+-----------------+-----------------------

In [32]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "2ff27739-a43f-4ad7-973a-4a3c9b9bdf3e"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|2ff27739-a43f-4ad...|2018-01-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-02-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-03-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-04-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-05-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-06-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-07-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-08-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-09-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-10-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-11-01|BAIXADO|
|2ff27739-a43f-4ad...|2018-12-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-01-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-02-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-03-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-04-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-05-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-06-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-07-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-08-01|BAIXADO|
|2ff27739-a43f-4ad...|2019-09-01|B

### Teste 4

In [36]:

# Definir o UUID que deseja filtrar
uuid_alvo = "bd57c75c-03f9-4f64-aecb-c0026f173c48"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show(truncate=False)

+------------------------------------+------------------------------------+------------------------------------+-------------------+------------------+-----------------+------------------+-----------------------+------------------+-----------------------+
|uuid                                |uuid_contract                       |uuid_customer                       |churn_date         |motivation        |churn_type       |data_source_insert|created_at             |data_source_update|updated_at             |
+------------------------------------+------------------------------------+------------------------------------+-------------------+------------------+-----------------+------------------+-----------------------+------------------+-----------------------+
|6e0d434a-bacb-411f-929a-a68478df8743|6e370c01-a85b-4ff0-870f-f54d2dff40bf|bd57c75c-03f9-4f64-aecb-c0026f173c48|2021-01-04 08:08:59|ENCER DE ATIVIDADE|90 DIAS BLOQUEADO|signet            |2024-04-26 20:36:23.557|                  |2

In [40]:
# Definir o UUID que deseja filtrar
uuid_alvo = "bd57c75c-03f9-4f64-aecb-c0026f173c48"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [39]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "6e370c01-a85b-4ff0-870f-f54d2dff40bf"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+-------+
|       uuid_contract|issue_date| status|
+--------------------+----------+-------+
|6e370c01-a85b-4ff...|2020-02-01| ABERTO|
|6e370c01-a85b-4ff...|2020-03-01|BAIXADO|
|6e370c01-a85b-4ff...|2020-04-01|BAIXADO|
|6e370c01-a85b-4ff...|2020-05-01|BAIXADO|
|6e370c01-a85b-4ff...|2020-06-01|BAIXADO|
|6e370c01-a85b-4ff...|2020-07-01|BAIXADO|
|6e370c01-a85b-4ff...|2020-08-01| ABERTO|
|6e370c01-a85b-4ff...|2020-09-01| ABERTO|
+--------------------+----------+-------+



### Teste 5

In [42]:
# Definir o UUID que deseja filtrar
uuid_alvo = "b99754d8-c214-44d0-9df0-79003a1516a0"

# Filtrar pelo UUID específico
churn_sdf_filtered = churn_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
churn_sdf_filtered.show()

+--------------------+--------------------+--------------------+-------------------+------------+--------------------+------------------+--------------------+------------------+--------------------+
|                uuid|       uuid_contract|       uuid_customer|         churn_date|  motivation|          churn_type|data_source_insert|          created_at|data_source_update|          updated_at|
+--------------------+--------------------+--------------------+-------------------+------------+--------------------+------------------+--------------------+------------------+--------------------+
|797887fd-72b6-46c...|73fc201c-1db1-4b8...|b99754d8-c214-44d...|2024-03-27 16:40:38|INSATISFACAO|90 DIAS PRÉ CANCE...|            signet|2024-04-26 20:36:...|                  |2024-04-26 20:36:...|
+--------------------+--------------------+--------------------+-------------------+------------+--------------------+------------------+--------------------+------------------+--------------------+



In [47]:
# Definir o UUID que deseja filtrar
uuid_alvo = "b99754d8-c214-44d0-9df0-79003a1516a0"

# Filtrar pelo UUID específico
contrato_sdf_filtered = contrato_sdf.filter(col("uuid_customer") == uuid_alvo)

# Mostrar o resultado
contrato_sdf_filtered.show()

+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+-----------------+-------------------------+------------------+--------------------+------------------+--------------------+---------+-----------+---------------------+
|                uuid|       uuid_customer|        uuid_partner|         uuid_wallet| uuid_business_model|  status|         start_date|           end_date|status_reason|consumption_value|access_fee|financial_fee|due_day|payment_frequency|max_ticket_value_in_month|data_source_insert|          created_at|data_source_update|          updated_at|uuid_user|entity_type|uuid_partner_contract|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------+-------------------+-------------------+-------------+-----------------+----------+-------------+-------+--

In [46]:
from pyspark.sql.functions import col

# Definir o UUID que deseja filtrar
uuid_alvo = "73fc201c-1db1-4b83-851e-328d5fa8df03"

# Filtrar pelo UUID específico, selecionar as colunas desejadas e ordenar pela issue_date em ordem crescente
recebivel_sdf_filtered = (
    recebivel_sdf
    .filter(col("uuid_contract") == uuid_alvo)
    .select("uuid_contract", "issue_date", "status")
    .orderBy(col("issue_date").asc())
)

# Mostrar o resultado
recebivel_sdf_filtered.show(1000000)

+--------------------+----------+---------+
|       uuid_contract|issue_date|   status|
+--------------------+----------+---------+
|73fc201c-1db1-4b8...|2022-11-01|  BAIXADO|
|73fc201c-1db1-4b8...|2022-12-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-01-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-02-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-03-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-04-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-05-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-06-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-07-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-08-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-09-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-10-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-11-01|  BAIXADO|
|73fc201c-1db1-4b8...|2023-12-01|CANCELADO|
+--------------------+----------+---------+

